In [1]:
import plotly.graph_objects as go
import numpy as np

In [2]:
rows, cols = 4, 4

x_target, y_target = np.random.randint(low = 1, high = 5, size = 2)

x = [j + 1 for i in range(rows) for j in range(cols)]
y = [i + 1 for i in range(rows) for j in range(cols)]

f = go.FigureWidget([go.Scatter(x=x, y=y, mode='markers')])

scatter = f.data[0]
colors = ['#a3a7e4'] * (rows * cols)
scatter.marker.color = colors
scatter.marker.size = [50] * (rows * cols)
f.layout.hovermode = 'closest'

f.update_layout(
    width=750,  
    height=750,
    xaxis=dict(
        scaleanchor='y',
        scaleratio=1,
        range=[0, cols + 1],
        showticklabels=False,  
        tickvals=[],          
    ),
    yaxis=dict(
        range=[0, rows + 1],
        showticklabels=False,  
        tickvals=[],           
    ),
    plot_bgcolor='white',  
    paper_bgcolor='white'  
)


def update_point(trace, points, selector):
    c = list(scatter.marker.color)
    s = list(scatter.marker.size)
    for i in points.point_inds:
        if x[i] == x_target and y[i] == y_target:  
            c[i] = '#bae2be' 
        else:
            c[i] = '#F08080'  
        s[i] = 50
    with f.batch_update():
        scatter.marker.color = c
        scatter.marker.size = s

scatter.on_click(update_point)

f


FigureWidget({
    'data': [{'marker': {'color': [#a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4,
                                   #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4,
                                   #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4,
                                   #a3a7e4],
                         'size': [50, 50, 50, 50, 50, 50, 50, 50, 50, 50, 50, 50,
                                  50, 50, 50, 50]},
              'mode': 'markers',
              'type': 'scatter',
              'uid': 'e83e2c73-8509-48e3-9886-af1db8a80856',
              'x': [1, 2, 3, 4, 1, 2, 3, 4, 1, 2, 3, 4, 1, 2, 3, 4],
              'y': [1, 1, 1, 1, 2, 2, 2, 2, 3, 3, 3, 3, 4, 4, 4, 4]}],
    'layout': {'height': 750,
               'hovermode': 'closest',
               'paper_bgcolor': 'white',
               'plot_bgcolor': 'white',
               'template': '...',
               'width': 750,
               'xaxis': {'range': [0, 5], 'scaleanchor': 'y', 'scaleratio': 1, 'showti

In [41]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from scipy.linalg import expm


rows, cols = 4, 4
n = rows * cols

x = [j + 1 for i in range(rows) for j in range(cols)]
y = [i + 1 for i in range(rows) for j in range(cols)]


def prob(phase, ts, target):
    G = np.ones((16, 16)) - np.eye(16)
    psi = (1/4) * np.ones(16, dtype=np.complex128)
    psi[0] *= np.exp(1j * phase)
    return [np.abs((expm(-1j * t * G) @ psi)[target])**2 for t in ts]

def target_term(phase, t):
    return np.exp(1j * 15 * t)*[(1/4)*np.exp(-1j * phase)]

def non_target_term(phase, t):
    return (1/4) * 15 * np.exp(1j * 15 * t)*(np.exp(-1j * 16 * t) - 1)*(1/(16))*np.exp(-1j * phase)

ts = np.arange(0, 1, 0.01)
phis = np.linspace(0, 2 * np.pi, 100)  

fig = make_subplots(
    rows=2, cols=2, shared_xaxes='columns',
    subplot_titles=("Probability of Measuring the Target", "Relative Probability", "Amplitude Contributions", None),
    specs=[
        [{"type": "xy"}, {"type": "xy", "rowspan": 2}], 
        [{"type": "xy"}, None]                           
    ],
)


phi = 0

colors = ["#F08080"] * n
colors[5] = "#bae2be"  

marker_sizes = n * [int(500 / n)]

jitter_strength = 0.0015  # Adjust this value for more or less jitter

y_prob = prob(0, ts, 0)
y_prob_jittered = y_prob + np.random.normal(0, jitter_strength, size=len(y_prob))

y_target_term = np.abs(target_term(0, ts)) * np.real(target_term(0, ts))
y_target_term_jittered = y_target_term + np.random.normal(0, jitter_strength, size=len(y_target_term))

y_non_target_term = np.abs(non_target_term(0, ts)) * np.imag(non_target_term(0, ts))
y_non_target_term_jittered = y_non_target_term + np.random.normal(0, jitter_strength, size=len(y_non_target_term))

trace1 = go.Scatter(
    x=ts,
    y=y_prob_jittered,
    mode='lines',
    line=dict(color='black', width=2, dash='solid'),
    name="Probability to Measure the Target",
    line_shape='spline'
)

trace2 = go.Scatter(
    x=ts,
    y=y_target_term_jittered,
    mode='lines',
    line=dict(color='Blue', width=2, dash='dash'),
    name="Amplitude from the Target",
        line_shape='spline'
)

trace3 = go.Scatter(
    x=ts,
    y=y_non_target_term_jittered,
    mode='lines',
    line=dict(color='Black', width=2, dash='dot'),
    name="Amplitude From Other States",
    line_shape='spline'
)

trace4 = go.Scatter(
    x=x, y=y, mode='markers',
    name = "Relative Probability", 
    marker=dict(size=marker_sizes, color=colors)
)

fig.add_trace(trace1, row=1, col=1)
fig.add_trace(trace2, row=2, col=1)
fig.add_trace(trace3, row=2, col=1)
fig.add_trace(trace4, row=1, col=2)

steps = []
for phi in phis:
    y_prob = prob(phi, ts, 0)
    y_prob_jittered = y_prob + np.random.normal(0, jitter_strength, size=len(y_prob))

    y_target_term = np.abs(target_term(phi, ts)) * np.real(target_term(phi, ts))
    y_target_term_jittered = y_target_term + np.random.normal(0, jitter_strength, size=len(y_target_term))

    y_non_target_term = np.abs(non_target_term(phi, ts)) * np.imag(non_target_term(phi, ts))
    y_non_target_term_jittered = y_non_target_term + np.random.normal(0, jitter_strength, size=len(y_non_target_term))

    marker_sizes = np.empty(16, dtype=int)
    marker_sizes[:] = int(500 * prob(phi, [ts[np.argmax(prob(phi, ts, 1))]], 1)[0])
    marker_sizes[5] = int(500 * prob(phi, [ts[np.argmax(prob(phi, ts, 0))]], 0)[0])
    step = dict(
        method="update",
        args=[
            {
                "y": [
                    y_prob_jittered,
                    y_target_term_jittered,
                    y_non_target_term_jittered,
                    y
                ],
                "marker": [
                    None,
                    None,
                    None,
                    {"size": marker_sizes, "color": colors}  
                ]
            }
        ],
        label=f"{np.degrees(phi):.0f}°"  
    )
    steps.append(step)

sliders = [dict(
    active=0,  
    pad={"t": 50},
    steps=steps,
    currentvalue={"prefix": "Phase angle between target and non-target states: "}
)]

fig.update_yaxes(range=[0, 0.59], row=1, col=1)
fig.update_yaxes(range=[-0.6, 0.6], row=2, col=1)


fig.update_xaxes(showticklabels=False, row=1, col=2)
fig.update_yaxes(showticklabels=False, row=1, col=2)

#fig.update_xaxes(title_text='time', row=2, col=1)


fig.update_layout(
    sliders=sliders,
    width=2 * 300, height=672,
    showlegend=False,   
    margin=dict(t=50),   
    font=dict(family="Comic Sans MS, sans-serif", size=16, color="black"),
    plot_bgcolor='white',
    xaxis3=dict(showgrid=False, zeroline=True),
    yaxis3=dict(showgrid=True, zeroline=True, zerolinewidth=4, zerolinecolor='Green'),
                  # xaxis2=dict(showgrid=False, zeroline=False),
                  # yaxis2=dict(showgrid=True, zeroline=False),

)

fig.update_xaxes(showgrid=True, row=1, col=1)
fig.update_yaxes(showgrid=True, row=1, col=1)

xaxis_domain = fig.layout.xaxis2.domain
yaxis_domain = fig.layout.yaxis2.domain

# fig.add_shape(
#     type="rect",
#     xref="paper",
#     yref="paper",
#     x0=xaxis_domain[0],
#     y0=yaxis_domain[0],
#     x1=xaxis_domain[1],
#     y1=yaxis_domain[1],
#     fillcolor="white",
#     line=dict(width=0),
#     layer="below"
# )

fig.show()


In [1]:
# here lets import and set some python/jupyter preliminaries
# you don't need to do much here other than run the cell
%matplotlib widget
#%matplotlib ipympl
#%matplotlib inline
#%matplotlib notebook

# generic python libraries
import sys, os

# import some useful wrappers
dir_path = os.path.abspath("")
sys.path.append(dir_path)
from useful_wrappers import *

In [2]:
fig = GroversGrid(4,4)
fig 

FigureWidget({
    'data': [{'marker': {'color': [#a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4,
                                   #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4,
                                   #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4, #a3a7e4,
                                   #a3a7e4],
                         'line': {'color': 'DarkSlateGrey', 'width': 2},
                         'size': [50, 50, 50, 50, 50, 50, 50, 50, 50, 50, 50, 50,
                                  50, 50, 50, 50]},
              'mode': 'markers',
              'type': 'scatter',
              'uid': '81e3f787-ed04-4dec-9e1c-92f098ab9c36',
              'x': [1, 2, 3, 4, 1, 2, 3, 4, 1, 2, 3, 4, 1, 2, 3, 4],
              'y': [1, 1, 1, 1, 2, 2, 2, 2, 3, 3, 3, 3, 4, 4, 4, 4]}],
    'layout': {'height': 512.4999999999999,
               'hovermode': 'closest',
               'paper_bgcolor': 'white',
               'plot_bgcolor': 'white',
               'template': '...',
               'title': {'te

In [3]:
fig = GroverSearch(4,4)
fig 

In [55]:
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
from scipy.linalg import expm


rows, cols = 3, 3
x = [j + 1 for i in range(rows) for j in range(cols)]
y = [i + 1 for i in range(rows) for j in range(cols)]
n = rows * cols


def prob(phase, ts, target, n):
    G = np.ones((n, n)) - np.eye(n)
    psi = (1/np.sqrt(n)) * np.ones(n, dtype=np.complex128)
    psi[0] *= np.exp(1j * phase)
    return [np.abs((expm(-1j * t * G) @ psi)[target])**2 for t in ts]

def target_term(phase, t, n):
    return np.exp(1j * (n-1) * t)*[(1/np.sqrt(n))*np.exp(-1j * phase)]

def non_target_term(phase, t, n):
    return (1/np.sqrt(n)) * (n-1) * np.exp(1j * (n-1) * t)*(np.exp(-1j * n * t) - 1)*(1/(n))*np.exp(-1j * phase)

ts = np.arange(0, 1, 0.01)
phis = np.linspace(0, 2 * np.pi, 100)  

fig = make_subplots(
    rows=2, cols=2, shared_xaxes='columns',
    subplot_titles=("Probability of Measuring the Target", "Relative Probability", "Amplitude Contributions", None),
    specs=[
        [{"type": "xy"}, {"type": "xy", "rowspan": 2}], 
        [{"type": "xy"}, None]                           
    ],
)


phi = 0

colors = ["#F08080"] * n
colors[5] = "#bae2be"  

marker_sizes = n * [int(500 / n)]

jitter_strength = 0.0015  # Adjust this value for more or less jitter

y_prob = prob(0, ts, 0, n)
y_prob_jittered = y_prob + np.random.normal(0, jitter_strength, size=len(y_prob))

y_target_term = np.abs(target_term(0, ts, n)) * np.real(target_term(0, ts, n))
y_target_term_jittered = y_target_term + np.random.normal(0, jitter_strength, size=len(y_target_term))

y_non_target_term = np.abs(non_target_term(0, ts, n)) * np.imag(non_target_term(0, ts, n))
y_non_target_term_jittered = y_non_target_term + np.random.normal(0, jitter_strength, size=len(y_non_target_term))

trace1 = go.Scatter(
    x=ts,
    y=y_prob_jittered,
    mode='lines',
    line=dict(color='black', width=2, dash='solid'),
    name="Probability to Measure the Target",
    line_shape='spline'
)

trace2 = go.Scatter(
    x=ts,
    y=y_target_term_jittered,
    mode='lines',
    line=dict(color='Blue', width=2, dash='dash'),
    name="Amplitude from the Target",
        line_shape='spline'
)

trace3 = go.Scatter(
    x=ts,
    y=y_non_target_term_jittered,
    mode='lines',
    line=dict(color='Black', width=2, dash='dot'),
    name="Amplitude From Other States",
    line_shape='spline'
)

trace4 = go.Scatter(
    x=x, y=y, mode='markers',
    name = "Relative Probability", 
    marker=dict(size=marker_sizes, color=colors)
)

fig.add_trace(trace1, row=1, col=1)
fig.add_trace(trace2, row=2, col=1)
fig.add_trace(trace3, row=2, col=1)
fig.add_trace(trace4, row=1, col=2)

steps = []
for phi in phis:
    y_prob = prob(phi, ts, 0, n)
    y_prob_jittered = y_prob + np.random.normal(0, jitter_strength, size=len(y_prob))

    y_target_term = np.abs(target_term(phi, ts, n)) * np.real(target_term(phi, ts, n))
    y_target_term_jittered = y_target_term + np.random.normal(0, jitter_strength, size=len(y_target_term))

    y_non_target_term = np.abs(non_target_term(phi, ts, n)) * np.imag(non_target_term(phi, ts, n))
    y_non_target_term_jittered = y_non_target_term + np.random.normal(0, jitter_strength, size=len(y_non_target_term))

    marker_sizes = np.empty(n, dtype=int)
    marker_sizes[:] = int(500 * prob(phi, [ts[np.argmax(prob(phi, ts, 1, n))]], 1, n)[0])
    marker_sizes[5] = int(500 * prob(phi, [ts[np.argmax(prob(phi, ts, 0, n))]], 0, n)[0])
    step = dict(
        method="update",
        args=[
            {
                "y": [
                    y_prob_jittered,
                    y_target_term_jittered,
                    y_non_target_term_jittered,
                    y
                ],
                "marker": [
                    None,
                    None,
                    None,
                    {"size": marker_sizes, "color": colors}  
                ]
            }
        ],
        label=f"{np.degrees(phi):.0f}°"  
    )
    steps.append(step)

sliders = [dict(
    active=0,  
    pad={"t": 50},
    steps=steps,
    currentvalue={"prefix": "Phase angle between target and non-target states: "}
)]

fig.update_yaxes(range=[0, 0.59], row=1, col=1)
fig.update_yaxes(range=[-0.6, 0.6], row=2, col=1)


fig.update_xaxes(showticklabels=False, row=1, col=2)
fig.update_yaxes(showticklabels=False, row=1, col=2)

#fig.update_xaxes(title_text='time', row=2, col=1)


fig.update_layout(
    sliders=sliders,
    width=2 * 300, height=672,
    showlegend=False,   
    margin=dict(t=50),   
    font=dict(family="Comic Sans MS, sans-serif", size=16, color="black"),
    plot_bgcolor='white',
    xaxis3=dict(showgrid=False, zeroline=True),
    yaxis3=dict(showgrid=True, zeroline=True, zerolinewidth=4, zerolinecolor='Green'),
                  # xaxis2=dict(showgrid=False, zeroline=False),
                  # yaxis2=dict(showgrid=True, zeroline=False),

)

fig.update_xaxes(showgrid=True, row=1, col=1)
fig.update_yaxes(showgrid=True, row=1, col=1)

xaxis_domain = fig.layout.xaxis2.domain
yaxis_domain = fig.layout.yaxis2.domain

# fig.add_shape(
#     type="rect",
#     xref="paper",
#     yref="paper",
#     x0=xaxis_domain[0],
#     y0=yaxis_domain[0],
#     x1=xaxis_domain[1],
#     y1=yaxis_domain[1],
#     fillcolor="white",
#     line=dict(width=0),
#     layer="below"
# )

fig.show()
